In [ ]:
# Copyright 2020 IITK EE604A Image Processing. All Rights Reserved.
# 
# Licensed under the MIT License. Use and/or modification of this code outside of EE604 must reference:
#
# © IITK EE604A Image Processing 
# https://github.com/ee604/ee604_assignments
#
# Author: Shashi Kant Gupta, Chiranjeev Prachand and Prof K. S. Venkatesh, Department of Electrical Engineering, IIT Kanpur

# Task 4 (Bonus Question): Video Stabilization

For this bonus question, you have to search and find a suitable solution to stabilize the provided shaky video. You are free to follow any approach/method or python modules to do this. Unless until following conditions satisfy:

* Any modules which you use should not be a direct implementation.
* By "stabilization," we do not mean a perfect solution. But it should be satisfactorily better than the original video.

In [1]:
%%bash
pip install git+https://github.com/ee604/ee604_plugins
pip install git+https://github.com/shashikg/google_colab_plugins
mkdir output

  Cloning https://github.com/ee604/ee604_plugins to /tmp/pip-req-build-yvplpmyh
  Created wheel for ee604-plugins: filename=ee604_plugins-0.4.2-cp36-none-any.whl size=2457 sha256=8f8aadde79124da6dd73281fa70c87c3788f95a1e2caf7b84b1208defe0b153b
  Stored in directory: /tmp/pip-ephem-wheel-cache-f7t_j1eq/wheels/34/a8/1d/ae3b7d209ecde89b4800a47ec55a61e7503bb9548bbb975806
Successfully built ee604-plugins
  Cloning https://github.com/shashikg/google_colab_plugins to /tmp/pip-req-build-6ilgm7_7
  Created wheel for google-colab-plugins: filename=google_colab_plugins-0.1-cp36-none-any.whl size=3075 sha256=aa1b08299ca1be78d0f26792ecef034335a7236d8e8d89ef62a17087169eb0ae
  Stored in directory: /tmp/pip-ephem-wheel-cache-ja14yde2/wheels/0d/7a/c0/f08e26849983b61cab0600b42d2547a3a963f611f738877eff
Successfully built google-colab-plugins


  Running command git clone -q https://github.com/ee604/ee604_plugins /tmp/pip-req-build-yvplpmyh
  Running command git clone -q https://github.com/shashikg/google_colab_plugins /tmp/pip-req-build-6ilgm7_7
mkdir: cannot create directory ‘output’: File exists


In [2]:
# Importing required libraries

import cv2
import numpy as np
from IPython.display import display
from PIL import Image
import matplotlib.pyplot as plt
from google_colab_plugins import playVideo

from ee604_plugins import download_dataset

download_dataset(assignment_no=4, task_no=4)

Download Complete!


In [3]:
orig_video_dir = "data/shaky_video.mp4"
stab_video_dir = "output/stab_video.mp4"

print("Original shaky video")
playVideo(filename=orig_video_dir)

Original shaky video


In [4]:
# Use the provided area to write your algorithm.
# Original video directory and filename: `orig_video_dir`
# Must save your stablized video inside output folder with name stab_video.mp4 | Use `stab_video_dir`

#############################
# Start your code from here #
#############################

#### Point Feature Matching method for video stablization
# Step 1: Input frame sequence
# Step 2: Optical flow measurement
# Step 3: Correspondence selection between point
# Step 4: Transform estimation from noisy correspondence
# Step 5: Applying transformation and smoothing
# Step 6: Writing frames to the file

!pip install scikit-video
from skvideo.io import FFmpegWriter as VideoWriter

# Function for smoothing a 1-D signal
def movingAverage(curve, radius): 
  window_size = 2 * radius + 1
  f = np.ones(window_size)/window_size 
  curve_pad = np.lib.pad(curve, (radius, radius), 'edge') 
  curve_smoothed = np.convolve(curve_pad, f, mode='same') 
  curve_smoothed = curve_smoothed[radius:-radius]
  return curve_smoothed 

# Function for applying moving average on each dimensions of trajectory (x, y & angle)
def smooth(trajectory): 
  smoothed_trajectory = np.copy(trajectory) 
  for i in range(3):
    smoothed_trajectory[:,i] = movingAverage(trajectory[:,i], radius=Smooth_radius)

  return smoothed_trajectory

# Fixing the border artifacts
def fixBorder(frame):
  s = frame.shape
  T = cv2.getRotationMatrix2D((s[1]/2, s[0]/2), 0, 1.14)
  frame = cv2.warpAffine(frame, T, (s[1], s[0]))
  return frame

# Global variable for smoothing radius
Smooth_radius = 80

# Create video reader
cap = cv2.VideoCapture(orig_video_dir)
n_frames = int(cap.get(cv2.CAP_PROP_FRAME_COUNT))
W = int(cap.get(cv2.CAP_PROP_FRAME_WIDTH)) 
H = int(cap.get(cv2.CAP_PROP_FRAME_HEIGHT))
fps = cap.get(cv2.CAP_PROP_FPS)

# Create video writer
out = VideoWriter(stab_video_dir, inputdict={'-r': str(fps)}, outputdict={'-r': str(fps)})

# Read first frame & convert into grayscale
_, prev = cap.read()
prev_gray = cv2.cvtColor(prev, cv2.COLOR_BGR2GRAY)

# Transform matrix containing translational and rotational parameters for each frame
transforms = np.zeros((n_frames-1, 3), np.float32) 

for i in range(n_frames-2):
  # Tracking patches of points
  prev_pts = cv2.goodFeaturesToTrack(prev_gray,
                                     maxCorners=200,
                                     qualityLevel=0.01,
                                     minDistance=30,
                                     blockSize=3)
  ret, curr = cap.read() 
  if not ret: 
    break 
  
  curr_gray = cv2.cvtColor(curr, cv2.COLOR_BGR2GRAY)

  # Optical flow calculation
  curr_pts, status, err = cv2.calcOpticalFlowPyrLK(prev_gray, curr_gray, prev_pts, None)

  # Sanity check
  assert prev_pts.shape == curr_pts.shape

  # Filtering relevant points for transformation parameters
  idx = np.where(status==1)[0]
  prev_pts = prev_pts[idx]
  curr_pts = curr_pts[idx]

  # Generating 2X3 transform matrix between previous and current frame
  m = cv2.estimateAffinePartial2D(prev_pts, curr_pts)[0]
  dx = m[0,2]
  dy = m[1,2]
  da = np.arctan2(m[1,0], m[0,0])

  # Storing parameters
  transforms[i] = [dx,dy,da]
  prev_gray = curr_gray

# Forming trajectory by taking cumulative sum of transform parametrs over row
trajectory = np.cumsum(transforms, axis=0)

# Smoothing the trajectory to reduce perturbations using moving average and forming the smooth transforms
smoothed_trajectory = smooth(trajectory)
difference = smoothed_trajectory - trajectory
transforms_smooth = transforms + difference

# Re-setting the frame reader at 0 position
cap.set(cv2.CAP_PROP_POS_FRAMES, 0) 

for i in range(n_frames-2):
  ret, frame = cap.read() 
  if not ret:
    break
    
  # Getting smooth transform parameters  
  dx = transforms_smooth[i,0]
  dy = transforms_smooth[i,1]
  da = transforms_smooth[i,2]

  # Forming transform matrix
  m = np.zeros((2,3), np.float32)
  m[0,0] = np.cos(da)
  m[0,1] = -np.sin(da)
  m[1,0] = np.sin(da)
  m[1,1] = np.cos(da)
  m[0,2] = dx
  m[1,2] = dy
  
  # Warping the frames according to the transform and writing into the file
  frame_stabilized = cv2.warpAffine(frame, m, (W,H))
  frame_stabilized = fixBorder(frame_stabilized)
  frame_stabilized = cv2.resize(frame_stabilized, (W,H))
  out.writeFrame(frame_stabilized)

cap.release()
out.close()
cv2.destroyAllWindows()

#############################
# End your code here ########
#############################

In [5]:
print("Stabilized video")
playVideo(filename=stab_video_dir)

Stabilized video
